In [53]:
import numpy as np
import matplotlib.pyplot as plt
import math
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
from tqdm import tqdm

In [54]:
plt.rcParams.update({'font.size': 12,
                     'axes.titlesize': 12,
                     'axes.labelsize': 18,
                     'lines.linewidth': 1,
                     'lines.markersize': 10,
                     'xtick.labelsize' : 10,
                     'ytick.labelsize' : 10,
                     'xtick.top' : True,
                     'xtick.direction' : 'in',
                     'ytick.right' : True,
                     'ytick.direction' : 'in',}) 

### An individual bird $i$ at position $r_{i}(t)$ propelling with a speed $v_{0}$ in the direction defined by the angle $\Theta_{i}(t)$ at time $t$ changes its direction to align with its neighbours within a distance $r$. 
### The dynamics is governed by the following 2 equations:

### (1) $\Theta_{i}(t+dt) = \langle \Theta_{j} \rangle _{|r_{i} - r_{j}|<r} + \eta $
### (2) $ r_{i}(t + dt) = r_{i}(t) + v_{0} \cdot dt \cdot \begin{bmatrix} \cos \Theta_{i}(t) \\ \sin \Theta_{i}(t) \end{bmatrix} $

### where $\eta$ is the uncertainty due to noise

In [55]:
#Define configuration
L = 50
rho_N = 0.8 #number density of agents
N = int(rho_N*(L**2)) #number of agents in the defined 2D space
eta = 0.12 #noise intensity
roi = 2 #radius of influence 
#dt = 0.01 #time step
dt = 1
velocity = 0.8 #propulsion velocity

In [56]:
#initialise the agent coordinates and orientations
#positions_x = np.random.uniform(0,L,N)
#positions_y = np.random.uniform(0,L,N)
positions = np.random.uniform(0,L,size=(N,2))
orientations = np.random.uniform(-np.pi,np.pi,N)

In [57]:
#Intialise the animation
fig, ax= plt.subplots(figsize=(10,10))
ax.set_aspect('equal', adjustable='box')
# Set the background color to black
ax.set_facecolor('black') 
ax.set_xlim(0, 50)
ax.set_ylim(0, 50)
ax.set_title('Initial state')
q_plot = ax.quiver(positions[:,0], positions[:,1], np.cos(orientations), np.sin(orientations), np.degrees(orientations), clim=[-180, 180],cmap='hsv'
                  ,scale=60,headwidth=13,headlength=8,headaxislength=5)
fig.colorbar(q_plot, ax=ax)

In [58]:
def get_neighbours(x0,y0,positions,roi):
    ##Returns ids (index) of all neighbours within radius of influence of the particle 
    noi = [] #neighbours of influence
    for i,(x,y) in enumerate(positions):
        distance = np.sqrt((x-x0)**2 + (y-y0)**2)
        if distance < roi:
            noi.append(i)
    return(noi)

In [59]:
def get_avg_unit_vector(noi,orientations):
    unit_vec_list = []
    for i in noi:
        theta = orientations[i]
        vec = np.array([np.cos(theta),np.sin(theta)])
        mag = np.sqrt(vec[0]**2 + vec[1]**2)
        unit_vec = vec/mag
        unit_vec_list.append(unit_vec)
    avg_unit_vec = np.mean(np.array(unit_vec_list),axis=0)
    return(avg_unit_vec)

In [60]:
#Intialise the animation
fig, ax= plt.subplots(figsize=(10,10))
ax.set_aspect('equal', adjustable='box')
#ax.set_axis_off()
# Set the background color to black
ax.set_facecolor('black') 
q_plot = ax.quiver(positions[:,0], positions[:,1], np.cos(orientations), np.sin(orientations), np.degrees(orientations), clim=[-180, 180], cmap='hsv'
                  ,scale=80,headwidth=13,headlength=8,headaxislength=5)
ax.set_xlim(0, 50)
ax.set_xlim(0, 50)
fig.tight_layout()
plt.close()

#tqdm progress bar
progress_bar = tqdm(total=total_steps, position=0, desc="Progress")

def animate(f):
    #print(f)
    progress_bar.update(1)
    for i,(xi,yi) in enumerate(positions):
        neighbours = get_neighbours(xi,yi,positions,roi)
        avg_unit_vector = get_avg_unit_vector(neighbours,orientations)
        noise_vector = eta*np.random.uniform(-np.pi,np.pi,2)

        #new orientation
        new_orientation_vec = avg_unit_vector + noise_vector
        
        #compute new position
        positions[i,:] += (new_orientation_vec)*dt*velocity

        #compute new orientation
        orientations[i] = math.atan2(new_orientation_vec[1],new_orientation_vec[0]) #convert orientation vector into orientation angle

    #implement periodic boundary condition
    positions[positions>L] -= L
    positions[positions<0] += L
    
    # Set the new vector data to the quiver plot
    q_plot.set_offsets(positions)
    q_plot.set_UVC(np.cos(orientations), np.sin(orientations), np.degrees(orientations))
    return q_plot,

Progress: 108it [23:15, 12.92s/it]                                                              | 0/70 [00:00<?, ?it/s]


In [61]:
total_steps = 70
anim = FuncAnimation(fig,animate,frames=np.arange(0,total_steps),interval=100, blit=True)
HTML(anim.to_html5_video())

Progress: 73it [13:45, 11.21s/it]                                                                                      